<a href="https://colab.research.google.com/github/sclaudiobr/covid2019/blob/master/COVID19_Heatmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install --upgrade folium

ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.11.0 which is incompatible.
  Found existing installation: folium 0.8.3
    Uninstalling folium-0.8.3:
      Successfully uninstalled folium-0.8.3


In [125]:
import pandas as pd
import numpy as np
import folium
from folium import plugins
import json
print("Nova versão do Folium: ", folium.__version__)

Nova versão do Folium:  0.11.0


In [ ]:
# Aqui, configuramos o acesso ao reposiório e exportação para o formato pandas Dataframe (tabela)
# Observe que aqui usei o terminal LINUX do COLAB para a importacao e descompactação do arquivo.
!wget https://data.brasil.io/dataset/covid19/caso.csv.gz
!gunzip caso.csv.gz
df = pd.read_csv("caso.csv")
df.head(10)

In [129]:
# Importa dados de localização ponto(lat,long)) das cidades segundo a base de dados do IBGE de 2010
cidades = pd.read_csv('https://raw.githubusercontent.com/sandeco/CanalSandeco/master/covid-19/cidades_brasil.csv')
cidades.head()

codigo_ibge                 nome  latitude  longitude  capital  codigo_uf
0      5200050      Abadia de Goiás -16.75730   -49.4412        0         52
1      3100104  Abadia dos Dourados -18.48310   -47.3916        0         31
2      5200100            Abadiânia -16.19700   -48.7057        0         52
3      3100203               Abaeté -19.15510   -45.4444        0         31
4      1500107           Abaetetuba  -1.72183   -48.8788        0         15

In [130]:
# Aqui fazemos a troca de índice de cidades pelo códifo do IBGE
cidades = cidades.set_index('codigo_ibge')

In [93]:
cidades.head()

nome  latitude  longitude  capital  codigo_uf
codigo_ibge                                                              
5200050          Abadia de Goiás -16.75730   -49.4412        0         52
3100104      Abadia dos Dourados -18.48310   -47.3916        0         31
5200100                Abadiânia -16.19700   -48.7057        0         52
3100203                   Abaeté -19.15510   -45.4444        0         31
1500107               Abaetetuba  -1.72183   -48.8788        0         15

In [136]:
cities = df.loc[df.place_type == 'city',:]
cities.place_type.unique()

array(['city'], dtype=object)

In [137]:
# juntar as duas bases de dados (IBGE cidades) come guardar na variável cities
cities = cities.join(cidades, on='city_ibge_code')

In [138]:
# selecionar as colunas de interesse da tabela "cities", 
# geo_last são os ultimos registros da tabela para cada cidade
geo_last = cities.loc[cities.is_last==True,['city','latitude', 'longitude','state','confirmed','deaths']]
geo_last.head()

city  latitude  longitude state  confirmed  deaths
114    Acrelândia  -9.82581   -66.8972    AC        211       3
212  Assis Brasil -10.92980   -69.5738    AC        206       5
277     Brasiléia -10.99500   -68.7497    AC        465       7
334        Bujari  -9.81528   -67.9550    AC        237       3
422      Capixaba -10.56600   -67.6860    AC        159       5

In [139]:
#Quantidade de cidades com casos de covid-19
len(geo_last)

5315

In [100]:
#Quantidade de casos confirmados 
geo_last.confirmed.sum()

1703235

In [140]:
#Quantidade de mortes por covid-19
geo_last.deaths.sum()

67628

In [141]:
#Porcentagem de mortos sobre os casos confirmados
geo_last.deaths.sum()/geo_last.confirmed.sum()*100

3.9705619013230704

In [142]:
# verificar se todos os estados estão inseridos
len(geo_last.state.unique())

27

In [143]:
coordenadas = geo_last[['latitude','longitude','confirmed']]
#retirar as linhas que tiver dados faltando
coordenadas = coordenadas.dropna()
coordenadas.head()

latitude  longitude  confirmed
114  -9.82581   -66.8972        211
212 -10.92980   -69.5738        206
277 -10.99500   -68.7497        465
334  -9.81528   -67.9550        237
422 -10.56600   -67.6860        159

In [144]:
baseMap = folium.Map(
    width = '100%',   height = '100%',
    location = [-15.77972, -47.92972], # <- Brasil
    zoom_start = 4
)

In [145]:
baseMap

In [146]:
baseMap = baseMap.add_child(plugins.HeatMap(coordenadas))

In [147]:
baseMap

In [148]:
# retirar dados faltantes
geo_last = geo_last.dropna()
geo_last.head(5)

city  latitude  longitude state  confirmed  deaths
114    Acrelândia  -9.82581   -66.8972    AC        211       3
212  Assis Brasil -10.92980   -69.5738    AC        206       5
277     Brasiléia -10.99500   -68.7497    AC        465       7
334        Bujari  -9.81528   -67.9550    AC        237       3
422      Capixaba -10.56600   -67.6860    AC        159       5

In [149]:
for i in range(0,len(geo_last)):
    folium.Circle(
        location = [geo_last.iloc[i]['latitude'], geo_last.iloc[i]['longitude']],
        color = '#00FF69',
        fill = '#00A1B3',
        tooltip = '<li><bold> CIDADE: '+ str(geo_last.iloc[i]['city']) + "</li></bold>" +
                 '<li><bold> ESTADO: '+ str(geo_last.iloc[i]['state']) +"</li></bold>" +
                 '<li><bold> CONFIRMADOS: '+ str(geo_last.iloc[i]['confirmed'])+"</li></bold>" +
                 '<li><bold> MORTES: '+ str(geo_last.iloc[i]['deaths']) + "</li></bold>" ,
        radius = (geo_last.iloc[i]['confirmed']**1.1)
                                            
    ).add_to(baseMap)

In [150]:
# importando logomarca e colocando no mapa
from folium.plugins import FloatImage
url = 'https://raw.githubusercontent.com/sclaudiobr/algoritmos-py/master/text43.png'
FloatImage(url,bottom=10,left=55).add_to(baseMap)
baseMap

In [151]:
baseMap.save('heatmap-cidade.html')